## CAB420 Final Assignment


# Importing Library and Read Data from CSV files


In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import random

# Spliting data to trainning and testing set
from sklearn.model_selection import train_test_split
# Fitting Multiple Linear Regression to the trainning set
from sklearn.linear_model import LinearRegression, Lasso
from sklearn.cluster import KMeans
from sklearn.metrics import mean_squared_error, r2_score

# Matplotlib setting 
%config InlineBackend.print_figure_kwargs = {'bbox_inches':None}
%config InlineBackend.rc = {'font.size': 30, 'figure.figsize': (30.0, 20.0), 'figure.facecolor': (1, 1, 1, 0), 'figure.subplot.bottom': 0.125, 'figure.edgecolor': (1, 1, 1, 0), 'figure.dpi': 500}

## Data Preprocessing

In [2]:
# Import dataset
rating_dataset = pd.read_csv("./data/ratings.csv")
movies_dataset = pd.read_csv("./data/movies.csv")

# Set the index by movieId, This line of code only able to execute once
movies_dataset.set_index('movieId', inplace = True)

# Convert genres to dummy variable dataset
# movies_genres_dummy <- a dataframe contains the genres values for all the movies and using movieId as index
movies_genres_dummy = movies_dataset['genres'].str.get_dummies(sep='|')
# Remove (no genres listed) from dummy because all 0 can represent (no genres listed)
movies_genres_dummy = movies_genres_dummy.drop(columns=["(no genres listed)"], axis=1)


# Use this If you think you are able to work on the years 
# Cannot use year as parameter because in movie 3xxxx there is a movie does not have years
# movies_dataset["year"] = movies_dataset["title"].str.extract(r"\(([0-9]+)\)").astype(dtype=np.int)

# Pre Processing for KMeans Algorithm finding the similar movies
movies_dataset = movies_dataset.drop(columns=["genres"], axis=1)
movies_dataset = pd.merge(movies_dataset, movies_genres_dummy, on = 'movieId', how = "left")


## Combine Rating and Movie Dataset to one Dataset

In [3]:
full_rating_dataset = pd.merge(rating_dataset[["userId","movieId","rating"]], movies_genres_dummy, on = 'movieId', how = "left")

full_rating_dataset['rating'] = full_rating_dataset['rating'] * 2
full_rating_dataset['rating'] = full_rating_dataset['rating'].astype(int)

genres = full_rating_dataset.iloc[:,3:].columns

# # Adeventure Value for this movie
# movies_dataset.iloc[1,:]["Adventure"]

# for idx, genre in enumerate(genres):
#     movies_dataset.loc[movies_dataset[genre] == 1,"genre"] += 2**idx

# movies_dataset.to_csv("test.csv")

In [4]:
full_rating_dataset

userId  movieId  rating  Action  Adventure  Animation  Children  \
0            1        1       8       0          1          1         1   
1            1        3       8       0          0          0         0   
2            1        6       8       1          0          0         0   
3            1       47      10       0          0          0         0   
4            1       50      10       0          0          0         0   
5            1       70       6       1          0          0         0   
6            1      101      10       0          1          0         0   
7            1      110       8       1          0          0         0   
8            1      151      10       1          0          0         0   
9            1      157      10       0          0          0         0   
10           1      163      10       1          0          0         0   
11           1      216      10       0          0          0         0   
12           1      223       6       0          0          0         0   
13           1      231      10       0          1          0         0   
14           1      235       8       0          0          0         0   
15           1      260      10       1          1          0         0   
16           1      296       6       0          0          0         0   
17           1      316       6       1          1          0         0   
18           1      333      10       0          0          0         0   
19           1      349       8       1          0          0         0   
20           1      356       8       0          0          0         0   
21           1      362      10       0          1          0         1   
22           1      367       8       1          0          0         0   
23           1      423       6       1          0          0         0   
24           1      441       8       0          0          0         0   
25           1      457      10       0          0          0         0   
26           1      480       8       1          1          0         0   
27           1      500       6       0          0          0         0   
28           1      527      10       0          0          0         0   
29           1      543       8       0          0          0         0   
...        ...      ...     ...     ...        ...        ...       ...   
100806     610   150401       6       1          0          0         0   
100807     610   152077       8       0          0          0         0   
100808     610   152081       8       1          1          1         1   
100809     610   152372       7       0          0          0         0   
100810     610   155064       7       0          0          0         0   
100811     610   156371      10       0          0          0         0   
100812     610   156726       9       0          0          0         0   
100813     610   157296       8       0          1          1         0   
100814     610   158238      10       0          0          0         0   
100815     610   158721       7       1          0          0         0   
100816     610   158872       7       0          0          1         0   
100817     610   158956       6       1          0          0         0   
100818     610   159093       6       1          0          0         0   
100819     610   160080       6       1          0          0         0   
100820     610   160341       5       1          0          0         0   
100821     610   160527       9       1          0          0         0   
100822     610   160571       6       0          0          0         0   
100823     610   160836       6       1          0          0         0   
100824     610   161582       8       0          0          0         0   
100825     610   161634       8       0          0          0         0   
100826     610   162350       7       1          0          0         0   
100827     610   163937       7  

## Linear Regression for Predicting a user how many marks will he/she giving to a movie according to he/she previous rating to other movie and the others how they rate this movie


In [5]:
X_df = full_rating_dataset.drop(columns=['rating'], axis=1)
y_df = full_rating_dataset.iloc[:,2]

X = X_df.values
y = y_df.values

X_train, X_test, y_train, y_test = train_test_split(X,y, test_size = 0.3)

regressor = LinearRegression(normalize=True)
regressor.fit(X_train,y_train)

y_pred = regressor.predict(X_test)

y_pred

array([6.45902743, 6.97601419, 6.60326051, ..., 7.17613318, 6.99088922,
       6.58106962])

In [6]:
y_test

array([7, 4, 3, ..., 7, 7, 4])

In [7]:
regressor.score(X_test,y_test)

0.04267742023809895

## DecisionTree

In [8]:
from sklearn import tree
clf = tree.DecisionTreeClassifier()
clf = clf.fit(X_train, y_train)

clf.score(X_train,y_train)

1.0

In [9]:
clf.score(X_test,y_test)

0.23552940398664507

In [10]:
yhat = clf.predict(X_test)

yhat

array([2, 6, 6, ..., 8, 8, 5])

In [11]:
y_test

array([7, 4, 3, ..., 7, 7, 4])

KNN

# K-Means Algorithm Clustering Similar Movies

In [12]:
# The dataset will use in this case
movies_dataset.head()

title  Action  Adventure  Animation  \
movieId                                                                     
1                          Toy Story (1995)       0          1          1   
2                            Jumanji (1995)       0          1          0   
3                   Grumpier Old Men (1995)       0          0          0   
4                  Waiting to Exhale (1995)       0          0          0   
5        Father of the Bride Part II (1995)       0          0          0   

         Children  Comedy  Crime  Documentary  Drama  Fantasy  Film-Noir  \
movieId                                                                    
1               1       1      0            0      0        1          0   
2               1       0      0            0      0        1          0   
3               0       1      0            0      0        0          0   
4               0       1      0            0      1        0          0   
5               0       1      0            0      0        0          0   

         Horror  IMAX  Musical  Mystery  Romance  Sci-Fi  Thriller  War  \
movieId                                                                   
1             0     0        0        0        0       0         0    0   
2             0     0        0        0        0       0         0    0   
3             0     0        0        0        1       0         0    0   
4             0     0        0        0        1       0         0    0   
5             0     0        0        0        0       0         0    0   

         Western  
movieId           
1              0  
2              0  
3              0  
4              0  
5              0

In [13]:
# X only contains movie genres values
X = movies_dataset.iloc[:,1:].values

# Performs K = 1 to 50 for clustering the data
Ks = range(1,50)
# Array for saving inertias values for each K Clustering
inertias = []

# Loop K times 
for k in Ks:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X)
    inertias.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks,inertias,'-o')

## We Can see the result from the graph. The numbers of Inertias are dramatically decreased when k= 1 to k = 20, from 16000 to 6000. Then it becomes slow, from 6000 to 4000 when k = 21 to k=50. We should choose K = 20 in this case


In [14]:
# Create KMeans Algorithm to cluster the data in 20 groups 
model = KMeans(n_clusters = 20)

# Train KMeans
model.fit(X)

# Get the cluster values for each movie
labels = model.predict(X)

# Put the cluster value back to the dataset
movies_dataset['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
movies_dataset.sort_values(by=['cluster']).to_csv("MovieCluster.csv")

## Hierarchy Clustering Similar Users


We need to create a new dataframe from the full rating dataset
The new dataframe should contains all the average rating the user previous rating for all the genre

In [22]:
# Previous full rating dataframe
full_rating_dataset['rating'] = full_rating_dataset['rating'].astype(float) / 2
full_rating_dataset

userId  movieId  rating  Action  Adventure  Animation  Children  \
0            1        1     4.0       0          1          1         1   
1            1        3     4.0       0          0          0         0   
2            1        6     4.0       1          0          0         0   
3            1       47     5.0       0          0          0         0   
4            1       50     5.0       0          0          0         0   
5            1       70     3.0       1          0          0         0   
6            1      101     5.0       0          1          0         0   
7            1      110     4.0       1          0          0         0   
8            1      151     5.0       1          0          0         0   
9            1      157     5.0       0          0          0         0   
10           1      163     5.0       1          0          0         0   
11           1      216     5.0       0          0          0         0   
12           1      223     3.0       0          0          0         0   
13           1      231     5.0       0          1          0         0   
14           1      235     4.0       0          0          0         0   
15           1      260     5.0       1          1          0         0   
16           1      296     3.0       0          0          0         0   
17           1      316     3.0       1          1          0         0   
18           1      333     5.0       0          0          0         0   
19           1      349     4.0       1          0          0         0   
20           1      356     4.0       0          0          0         0   
21           1      362     5.0       0          1          0         1   
22           1      367     4.0       1          0          0         0   
23           1      423     3.0       1          0          0         0   
24           1      441     4.0       0          0          0         0   
25           1      457     5.0       0          0          0         0   
26           1      480     4.0       1          1          0         0   
27           1      500     3.0       0          0          0         0   
28           1      527     5.0       0          0          0         0   
29           1      543     4.0       0          0          0         0   
...        ...      ...     ...     ...        ...        ...       ...   
100806     610   150401     3.0       1          0          0         0   
100807     610   152077     4.0       0          0          0         0   
100808     610   152081     4.0       1          1          1         1   
100809     610   152372     3.5       0          0          0         0   
100810     610   155064     3.5       0          0          0         0   
100811     610   156371     5.0       0          0          0         0   
100812     610   156726     4.5       0          0          0         0   
100813     610   157296     4.0       0          1          1         0   
100814     610   158238     5.0       0          0          0         0   
100815     610   158721     3.5       1          0          0         0   
100816     610   158872     3.5       0          0          1         0   
100817     610   158956     3.0       1          0          0         0   
100818     610   159093     3.0       1          0          0         0   
100819     610   160080     3.0       1          0          0         0   
100820     610   160341     2.5       1          0          0         0   
100821     610   160527     4.5       1          0          0         0   
100822     610   160571     3.0       0          0          0         0   
100823     610   160836     3.0       1          0          0         0   
100824     610   161582     4.0       0          0          0         0   
100825     610   161634     4.0       0          0          0         0   
100826     610   162350     3.5       1          0          0         0   
100827     610   163937     3.5  

In [23]:
def generate_avg_rating_df():
    #genres_list includes ['Action', 'Adventure', 'Animation', 'Children', etc...]
    genres_list = movies_genres_dummy.columns.values

    # Columns name variable for creating the new dataframe
    columns_name = ["userId"]
    # Create Columns name array
    for genres in genres_list:
        columns_name.append("AVG_" + genres + "_Rating")

    # initialize the dataframe     
    df = pd.DataFrame(columns=columns_name)

    for userId in range(1,full_rating_dataset['userId'].max() + 1):
        row_values = { 'userId': userId }
        for idx , genre in enumerate(genres_list):
            # Getting the user Dataframe for calculating the avg value for this genre
            user_df = full_rating_dataset.loc[(full_rating_dataset["userId"] == userId) & (full_rating_dataset[genre] == 1) ]
            # calculating the avg value for this genre
            avg = user_df["rating"].mean()

            row_values.update( { columns_name[idx + 1] : avg} )
            
        df = df.append( pd.Series(row_values), ignore_index = True )
    df[['userId']] = df[['userId']].astype(int)
    return df.fillna(0)


In [24]:
# generate avg rating dataframe
avg_df = generate_avg_rating_df()

avg_df.head()

userId  AVG_Action_Rating  AVG_Adventure_Rating  AVG_Animation_Rating  \
0       1           4.322222              4.388235              4.689655   
1       2           3.954545              4.166667              0.000000   
2       3           3.571429              2.727273              0.500000   
3       4           3.320000              3.655172              4.000000   
4       5           3.111111              3.250000              4.333333   

   AVG_Children_Rating  AVG_Comedy_Rating  AVG_Crime_Rating  \
0             4.547619           4.277108          4.355556   
1             0.000000           4.000000          3.800000   
2             0.500000           1.000000          0.500000   
3             3.800000           3.509615          3.814815   
4             4.111111           3.466667          3.833333   

   AVG_Documentary_Rating  AVG_Drama_Rating  AVG_Fantasy_Rating  \
0                0.000000          4.529412            4.297872   
1                4.333333          3.882353            0.000000   
2                0.000000          0.750000            3.375000   
3                4.000000          3.483333            3.684211   
4                0.000000          3.800000            4.142857   

   AVG_Film-Noir_Rating  AVG_Horror_Rating  AVG_IMAX_Rating  \
0                   5.0           3.470588         0.000000   
1                   0.0           3.000000         3.750000   
2                   0.0           4.687500         0.000000   
3                   4.0           4.250000         3.000000   
4                   0.0           3.000000         3.666667   

   AVG_Musical_Rating  AVG_Mystery_Rating  AVG_Romance_Rating  \
0            4.681818            4.166667            4.307692   
1            0.000000            4.000000            4.500000   
2            0.500000            5.000000            0.500000   
3            4.000000            3.478261            3.379310   
4            4.400000            4.000000            3.090909   

   AVG_Sci-Fi_Rating  AVG_Thriller_Rating  AVG_War_Rating  AVG_Western_Rating  
0           4.225000             4.145455        4.500000            4.285714  
1           3.875000             3.700000        4.500000            3.500000  
2           4.200000             4.142857        0.500000            0.000000  
3           2.833333             3.552632        3.571429            3.800000  
4           2.500000             3.555556        3.333333            3.000000

In [25]:
%matplotlib inline

from scipy.cluster.hierarchy import linkage, dendrogram
userRatings = avg_df.iloc[:,1:].values

mergings = linkage(userRatings, method='complete')

dendrogram(
    mergings,
    labels = range(0,611),
    leaf_rotation= 90,
)

plt.show()

In [26]:
# X only contains movie genres values
X2 = avg_df.iloc[:,1:].values

# Performs K = 1 to 50 for clustering the data
Ks2 = range(1,50)
# Array for saving inertias values for each K Clustering
inertias2 = []

# Loop K times 
for k in Ks2:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X2)
    inertias2.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks2,inertias2,'-o')

## From the Grpah above, We can see that the dramatic decrease stop around cluster = 14, So we use 14 to cluster the user group

In [20]:
from scipy.cluster.hierarchy import fcluster
labels = fcluster(mergings, 12, criterion = 'distance')

# Put the cluster value back to the dataset
avg_df['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
avg_df.sort_values(by=['cluster']).to_csv("User_Cluster.csv")
labels

array([ 72,  28,  18,  49,  80,  70,  41,  80,  70,  88,  28,  89,  20,
        79,  80,  57,  49,  49,  41,  61,  70,  39,  57,  84,  96,  16,
        70,  52,  49,  97,  60,  48,  70,  44,  68,  40,  78,  63,  70,
        66,  39,  52,  66, 110,  62,  66,  44, 106,  98,  38,  49,  62,
        29,  80,  15,  83,  52,  66,  58,  88,  20,  70,  49,  49,  26,
        70,  64,  52,  21,  62,  76,  28,  66,  30,  80,  44,  93,  85,
        30,  97, 108,  63,  61,  52,  99,  66, 105,  22,  63,  60,  52,
        83,  66,  80,  56,  70,  91,  84,  82,  66, 106,  80,  49,  70,
        49,  94,  81,  68,  52,  53,  63,  66,  73, 106,  70,  77,  80,
        27,  49, 110,  63,  49,  81,  74,  49,  68,  37,  29,  73,  78,
        57,  52,  80,  80,  51,  80,  49,  93,  85,  52,  70,  66,  61,
        63,  68,   6,  34,  95,   6, 103, 110,  56, 108,  96,  34,  49,
         5,  54,  88,  41, 104,  68, 109,  32,  77,  49,  70,  51,  62,
        80,  65,  65,  87,  80,   1,  81,  52,  62,  66,  74,  8